# Infraestructure Manager revenue maximization with GSA

## 0. Load libraries

In [1]:
%load_ext autoreload
%autoreload 2

import numpy as np

from src.entities import GSA

from copy import deepcopy
from math import cos, pi, e
from typing import List, Mapping, Union

## 1. Define corridor

As an example, we will use the Spanish south high-speed railway corridor.



In [2]:
# Define corridor

corridor = {"MAD": {
                "CIU": {
                    "COR": {
                        "SEV": {
                            "CAD": {}
                        },
                        "PGE": {
                            "ANT": {
                                "GRA": {},
                                "MAL": {}
                                    }
                                }
                            }
                        }
                    }
            }

### 1.1. Get lines from corridor

In [3]:
# Get lines from corridor

def get_lines(corridor: dict, path: Union[list, None]=None) -> list:
    """
    Get all the lines in the corridor
    
    Args:
        corridor (dict): dictionary with the corridor structure
        path (list, optional): list of nodes
    
    Returns:
        list of lines
    """
    if path is None:
        path = []

    lines = []
    for node, child in corridor.items():
        new_path = path + [node]
        if not child:  # If the node has no children, it is a leaf
            lines.append(new_path)
        else:
            lines.extend(get_lines(child, new_path))  # If the node has children, we call the function recursively

    return lines

get_lines(corridor)

[['MAD', 'CIU', 'COR', 'SEV', 'CAD'],
 ['MAD', 'CIU', 'COR', 'PGE', 'ANT', 'GRA'],
 ['MAD', 'CIU', 'COR', 'PGE', 'ANT', 'MAL']]

### 1.2. Sample a random line, and a random route from the line

In [4]:
def sample_line(lines: list) -> list:
    """
    Sample a random line from the list of lines
    
    Args:
        lines (list): list of lines
    
    Returns:
        list: random line
    """
    return lines[np.random.randint(len(lines))] 

def sample_route(line: list) -> list:
    """
    Sample a random route from line
    
    Args:
        line (list): list of stations
        
    Returns:
        list: random route
    """
    return line[np.random.randint(0, len(line)-1):]

lines = get_lines(corridor)

line = sample_line(lines)
print(f"Sampled line: {line}")

# Sample a random route from line (at least two stations)
route = sample_route(line)
print(f"Sampled route: {route}")

Sampled line: ['MAD', 'CIU', 'COR', 'SEV', 'CAD']
Sampled route: ['CIU', 'COR', 'SEV', 'CAD']


### 1.3 Generate random timetable for a route

- Times in minutes.
- Initial time is randomized between 0 and 24*60 (24 hours).
- The time between stations is also randomized between 30 and 120 minutes.
- The time to dwell at each station is randomized between 2 and 8 minutes.

In [5]:
def get_timetable(route: list) -> dict:
    """
    Generate random timetable for route r
    
    Args:
        route (list): list of stations
    
    Returns:
        dict: timetable
    """
    timetable = {}
    AT = np.random.randint(0, 24*60)
    DT = AT
    for i, sta in enumerate(route):
        if i == 0 or i == len(route)-1:
            timetable[sta] = (AT, AT)
        else:
            timetable[sta] = (AT, DT)
            
        AT += np.random.randint(30, 120)
        DT = AT + np.random.randint(2, 8)
        
    return timetable

get_timetable(route)

{'CIU': (552, 552), 'COR': (638, 640), 'SEV': (747, 754), 'CAD': (855, 855)}

## 2. Generate as many requested services as needed

In [6]:
# Generate random requested timetable in corridor for a day t

def get_schedule_request(n_services: int) -> dict:
    """
    Generate random timetable
    
    Args:
        n_services (int): number of services
    
    Returns:
        dict: timetable
    """
    return {i: get_timetable(sample_route(sample_line(lines))) for i in range(1, n_services+1)}

# Generate random schedule
schedule = get_schedule_request(3)
schedule

{1: {'ANT': (1202, 1202), 'MAL': (1279, 1279)},
 2: {'CIU': (1183, 1183),
  'COR': (1272, 1278),
  'PGE': (1308, 1314),
  'ANT': (1401, 1407),
  'MAL': (1443, 1443)},
 3: {'MAD': (120, 120),
  'CIU': (215, 219),
  'COR': (285, 288),
  'PGE': (343, 347),
  'ANT': (452, 456),
  'GRA': (504, 504)}}

## 3. Define feasibility function

A service $ i $ is feasible (can be scheduled and, therefore, $ S_i $ take the value 1) if the following condition is met:

$ | DT_{ij} - DT_{kj} | \geq security\_gap $

Where:
- $ DT_{ij} $ is the departure time for service $ i $ from station $ j $.
- $  DT_{kj} $ is the departure time for service $ k $ from the same station $ j $.

Inequality must be met for all services ($ k \neq j $) that also operate at station $ j $ for service $ i $ to be feasible.

1) Requests from the Railway Undertakings (RUs) are considered as a set of services that can be scheduled or not. The decision variable $ S_i $ is binary and takes the value 1 if the service $ i $ is scheduled and 0 otherwise.

Service ID |  RU   |          Trip          |              Requested schedule              | 
:---: |:-----:|:----------------------:|:--------------------------------------------:|
1 | Renfe |   `[MAD, BAR, FIG]`    |      `[(0, 0), (148, 152), (180, 180)]`      |
2 | Ouigo | `[MAD, ZAR, BAR, FIG]` | `[(8, 8), (28, 30), (165, 167), (210, 210)]` |
3 | Iryo  |   `[MAD, BAR, FIG]`    |     `[(30, 30), (180, 182), (225, 225)]`     |


2) Get conflict matrices for each service. A conflict matrix is a binary matrix of 0's and 1's. A 1 appears in the outputs of services (different from the one we are analyzing) that interferes with a station of the service in question.

Service 1: Has an interference with the service 2 at the departure from Madrid.

Service ID | MAD | BAR | FIG |
:---: | :---: | :---: | :---: |
1 | 0 | 0 | 0 |
2 | 1 | 0 | 0|
3 | 0 | 0 | 0 |

In order to be feasible, the following condition must be met:

$ R_{S_1} = (S_1 \cdot 0 + S_1 \cdot 1 + S_3 \cdot 0) + (S_1 \cdot 0 + S_1 \cdot 0 + S_3 \cdot 0) +(S_1 \cdot 0 + S_1 \cdot 1 + S_3 \cdot 0) = 0 $ \\

Service 2: Has an interference with the service 1 at the departure from Madrid.

ID servicio | MAD | ZAR | BAR | FIG |
:---: | :---: | :---: | :---: | :---: |
1 | 0 | 0 | 0 | 0 |
2 | 1 | 0 | 0 | 0|
3 | 0 | 0 | 0 | 0 |

In order to be feasible, the following condition must be met:

$ R_{S_2} = (S_1 \cdot 1 + S_1 \cdot 0 + S_3 \cdot 0) + (S_1 \cdot 0 + S_1 \cdot 0 + S_3 \cdot 0) +(S_1 \cdot 0 + S_1 \cdot 1 + S_3 \cdot 0) = 0 $ \\

Service 3: Does not have any interference with the other services.

ID servicio | MAD | BAR | FIG |
:---: |:---:| :---: | :---: |
1 |  0  | 0 | 0 |
2 |  0  | 0 | 0|
3 |  0  | 0 | 0 |

In order to be feasible, the following condition must be met:

$ R_{S_2} = (S_1 \cdot 0 + S_1 \cdot 0 + S_3 \cdot 0) + (S_1 \cdot 0 + S_1 \cdot 0 + S_3 \cdot 0) +(S_1 \cdot 0 + S_1 \cdot 1 + S_3 \cdot 0) \leq 0 $ \\

We can define a general restriction to check if the timetable is feasible or not:

$ S_1 \cdot R_{S_1} + S_2 \cdot R_{S_2} + S_2 \cdot R_{S_2} \leq 0$

This equation can be read as follows:

- If a service $ S_i $ is planned, then its restrictions $ R_{S_i} $ must be met. If the service $ S_i $ is not planned, its own interferences do not have to be taken into account.
- For the set of schedules to be feasible, there must be no conflict between any of the planned services (all the $ S_i $ that take the value $ 1 $)

In [289]:
from functools import lru_cache

class RevenueMaximization:
    """
    Class for the revenue maximization problem.
    """
    def __init__(self,
                 requested_schedule: Mapping[int, Mapping[str, Union[int, int]]],
                 revenue: Mapping[int, Mapping[str, Union[float, int]]],
                 safe_headway: int=10
                 ) -> None:
        """
        Constructor
        
        Args:
            requested_schedule (dict): requested schedule
        """
        self.requested_schedule = requested_schedule 
        self.revenue = revenue
        self.updated_schedule = deepcopy(requested_schedule)
        self.requested_times = self.get_real_vars()
        self.real_boundaries = self.get_real_boundaries()
        self.boundaries = {'real': self.real_boundaries, 'discrete': np.array([], dtype=float)}
        self.safe_headway = safe_headway
        self.feasible_schedules = []
        self.scheduled_trains = np.zeros(len(self.requested_schedule))
    
    @staticmethod
    def penalty_function(x: float, k: int) -> float:
        """
        Penalty function
        
        Args:
            x (float): x
            k (int): k
        
        Returns:
            float: penalty
        """
        return 1 - e**(-k * x**2) * ( (1/2) * cos(pi * x) + (1/2) )
    
    def get_revenue(self, 
                    solution: Mapping[str, List[Union[float, int]]],
                    update_schedule: bool=True) -> int:
        """
        Get IM revenue.
        
        Args:
            solution (dict): solution
        
        Returns:
            float: IM revenue
        """
        if update_schedule:
            self.update_schedule(solution)
        S_i = solution['discrete']
        
        im_revenue = 0
        for i, service in enumerate(self.requested_schedule):
            k = self.revenue[service]['k']
            departure_station = list(self.requested_schedule[service].keys())[0]
            departure_time_delta = abs(self.updated_schedule[service][departure_station][1] - self.requested_schedule[service][departure_station][1])
            tt_penalties = []
            for j, stop in enumerate(self.requested_schedule[service].keys()):
                if i == 0 or i == len(self.requested_schedule[service]) - 1:
                    continue
                tt_penalty = self.penalty_function(abs(self.updated_schedule[service][stop][1] - self.requested_schedule[service][stop][1]) / self.safe_headway, k)
                tt_penalties.append(tt_penalty * self.revenue[service]['tt_max_penalty'])
            dt_penalty = self.penalty_function(departure_time_delta / self.safe_headway, k) * self.revenue[service]['dt_max_penalty']
            im_revenue += self.revenue[service]['canon'] * S_i[i] - dt_penalty *  S_i[i] - np.sum(tt_penalties) *  S_i[i]
            
        return im_revenue
    
    def update_schedule(self, solution: Mapping[str, np.ndarray]):
        """
        Update schedule with the solution
        
        Args:
            solution (dict): solution
        """
        times = solution["real"] if solution["real"].size else self.get_real_vars()
        s_idx = 0
        for i, service in enumerate(self.updated_schedule):
                for j, stop in enumerate(self.updated_schedule[service]):
                    if j == 0 or j == len(self.updated_schedule[service]) - 1:
                        self.updated_schedule[service][stop] = (times[s_idx], times[s_idx])
                        s_idx += 1
                    else:
                        self.updated_schedule[service][stop] = (times[s_idx], times[s_idx+1])
                        s_idx += 2
    
    def _departure_time_feasibility(self, scheduling) -> bool:
        """
        Check if there are any conflicts with the departure times.
        
        Args:
            solution (dict): solution
        
        Returns:
            bool: True if the departure time is feasible, False otherwise
        """
        S_i = scheduling
        security_array = []

        # Get conflicts between services
        for service in self.updated_schedule:
            service_sec_arr = []  # Build security matrix for service (columns are stops, rows are other services)
            for service_k in self.updated_schedule:
              service_sec_row = [] 
              for stop in self.updated_schedule[service]:
                if service_k == service or stop not in self.updated_schedule[service_k]:
                  service_sec_row.append(0)
                  continue

                if abs(self.updated_schedule[service][stop][1] - self.updated_schedule[service_k][stop][1]) < self.safe_headway:
                  service_sec_row.append(1)
                else:
                  service_sec_row.append(0)
              service_sec_arr.append(service_sec_row)

            security_array.append(np.array(service_sec_arr))
            
        # Get array of conflicts. If there is a conflict, the dot product will be different from zero
        if not S_i.dot(np.array([np.sum(S_i.dot(ssa)) for ssa in security_array])):
            return True
        return False
    
    def _stop_times_feasibility(self, scheduling):
        """
        Check if the travel times are feasible. In order to be feasible, the travel times must be greater than the requested ones.
        
        Args:
            solution (dict): solution
        
        Returns:
            bool: True if the travel times are feasible, False otherwise
        """
        S_i = scheduling
        for i, service in enumerate(self.requested_schedule):
            if S_i[i] == 0:
                continue
            original_service_times = tuple(self.requested_schedule[service].values())
            updated_service_times = tuple(self.updated_schedule[service].values())
            for j in range(1, len(original_service_times)-1):
                original_st = original_service_times[j][1] - original_service_times[j][0]
                updated_st = updated_service_times[j][1] - updated_service_times[j][0]
                if updated_st < original_st:
                    return False
        return True
        
    def _travel_times_feasibility(self, scheduling) -> bool:
        """
        Check if the travel times are feasible. In order to be feasible, the travel times must be greater than the requested ones.
        
        Returns:
            bool: True if the travel times are feasible, False otherwise
        """
        S_i = scheduling
        for i, service in enumerate(self.requested_schedule):
            if S_i[i] == 0:
                continue
            original_service_times = tuple(self.requested_schedule[service].values())
            updated_service_times = tuple(self.updated_schedule[service].values())
            for j in range(len(original_service_times)-1):
                original_tt = original_service_times[j+1][0] - original_service_times[j][1]
                updated_tt = updated_service_times[j+1][0] - updated_service_times[j][1]
                if updated_tt < original_tt:
                    return False
        return True
    
    def _feasible_boundaries(self, solution) -> bool:
        """
        Check if the solution is within the boundaries
        
        Args:
            solution (dict): solution
        
        Returns:
            bool: True if the solution is within the boundaries, False otherwise
        """
        for i, rv in enumerate(solution["real"]):
            if rv < self.real_boundaries[i][0] or rv > self.real_boundaries[i][1]:
                return False 
        return True
         
    def is_feasible(self,
                    timetable: Mapping[str, np.array],
                    scheduling: np.array,
                    update_schedule: bool=True
                    ) -> bool:
        """
        Check if the solution is feasible
        
        Args:
            timetable (Mapping[str, np.array]): solution obtained from the optimization algorithm
            scheduling (np.array): scheduling
        
        Returns:
            bool: True if the solution is feasible, False otherwise
        """
        if update_schedule:
            self.update_schedule(timetable)
            
        if not self._feasible_boundaries(timetable):
            return False
        
        if (self._departure_time_feasibility(scheduling) and 
                self._travel_times_feasibility(scheduling) and 
                self._stop_times_feasibility(scheduling)):
            return True
        return False
    
    def get_real_vars(self):
        """
        Get real variables
        
        Returns:
            list: real variables with requested schedule times.
        """
        real_vars = []
        for service in self.requested_schedule:
            for i, stop in enumerate(self.requested_schedule[service]):
                if i == 0 or i == len(self.requested_schedule[service]) - 1:
                    real_vars.append(self.requested_schedule[service][stop][0])
                else: 
                    real_vars.append(self.requested_schedule[service][stop][0])
                    real_vars.append(self.requested_schedule[service][stop][1])

        return real_vars
    
    def get_real_boundaries(self):
        """
        Get real boundaries
        
        Returns:
            list: real boundaries
        """
        real_vars = self.get_real_vars()
        real_boundaries = []
        for rv in real_vars:
            real_boundaries.append((rv-10, rv+10))

        return np.array(real_boundaries, dtype=float)
    
    def update_feasible_schedules(self, timetable: Mapping[str, np.array]):
        """
        Get feasible scheduling
        
        Args:
            timetable (Mapping[str, np.array]): timetable
        """
        def truth_table(dim: int):
            if dim < 1:
                return [[]]
            sub_tt = truth_table(dim-1)
            return [row + [val] for row in sub_tt for val in [0, 1]]
        
        self.update_schedule(timetable)
        
        train_combinations = truth_table(len(self.requested_schedule))
        self.feasible_schedules = list(filter(lambda schdl: self.is_feasible(timetable, np.array(schdl), update_schedule=False), train_combinations))
    
    def get_best_schedule(self, timetable):
        """
        Get best schedule
        
        Args:
            solution (dict): solution
        
        Returns:
            dict: best schedule
        """
        self.update_feasible_schedules(timetable)
        best_schedule = None
        best_revenue = -np.inf
        for fs in self.feasible_schedules:
            revenue = self.get_revenue({'real': timetable['real'], 'discrete': fs}, update_schedule=False)
            if revenue > best_revenue:
                best_revenue = revenue
                best_schedule = fs
        return np.array(best_schedule)
    
    def get_fitness_gsa(self, timetable):
        """
        Get fitness
        
        Args:
            solution (dict): solution
        
        Returns:
            float: fitness
        """
        best_schedule = self.get_best_schedule(timetable)
        return self.get_revenue({'real': timetable['real'], 'discrete': best_schedule}, update_schedule=False), 0
    
    def feasible_services_times(self, timetable):
        """
        Check if the service is feasible
        
        Returns:
            bool: True if the service is feasible, False otherwise
        """
        self.update_schedule(timetable)
        if not self._feasible_boundaries(timetable):
            return False
        
        scheduling = np.ones(len(self.requested_schedule))
        if  self._travel_times_feasibility(scheduling) and self._stop_times_feasibility(scheduling):
            return True
        return False
            
    def get_initial_population(self, population_size: int):
        """
        Get initial population
        
        Returns:
            dict: initial population
        """
        identify_services = [service for service in self.requested_schedule for _ in range(len(self.requested_schedule[service])*2 - 2)]
        population = []
        for _ in range(population_size):
            proposed_times = deepcopy(self.requested_times)
            updated_boundaries = deepcopy(self.real_boundaries)
            for j in range(len(self.requested_times)):
                lower_bound, upper_bound = updated_boundaries[j]
                proposed_times[j] = np.round(np.random.uniform(lower_bound, upper_bound), 2)
                if j != len(self.requested_times) - 1 and identify_services[j+1] == identify_services[j]:
                    travel_time = self.requested_times[j+1] - self.requested_times[j]
                    updated_boundaries[j+1] = (proposed_times[j] + travel_time, updated_boundaries[j+1][1])
                
            population.append(proposed_times)
            
        return {'real': np.array(population), 'discrete': np.array([[] for _ in range(population_size)])}


In [290]:
schedule = get_schedule_request(20)

In [302]:
# Dummy schedule
schedule = {1: {'MAD': (0, 0), 'BAR': (148, 152), 'FIG': (180, 180)},
            2: {'MAD': (8, 8), 'ZAR': (28, 30), 'BAR': (165, 167), 'FIG': (210, 210)},
            3: {'MAD': (30, 30), 'BAR': (180, 182), 'FIG': (225, 225)}}

In [303]:
from scipy.stats import loguniform

np.random.seed(seed=22)

def get_revenue_behaviour(schedule: dict) -> dict:
    """
    Get revenue behaviour
    
    Args:
        schedule (dict): schedule
    
    Returns:
        dict: revenue behaviour
    """
    revenue = {}
    bias = [0.2, 0.35, 0.1]
    for service in schedule:
        b = np.random.choice(bias)
        base_price = 55 * len(schedule[service])
        canon = base_price + b * base_price
        k = loguniform.rvs(0.01, 100, 1)
        max_penalty = canon * 0.4
        dt_penalty = max_penalty * 0.35
        tt_penalty = (max_penalty - dt_penalty) / (len(schedule[service]) - 1)
        revenue[service] = {'canon': canon, 'k': k, 'dt_max_penalty': dt_penalty, 'tt_max_penalty': tt_penalty}
    return revenue

revenue = get_revenue_behaviour(schedule)
revenue

{1: {'canon': 222.75,
  'k': 7.424686268142557,
  'dt_max_penalty': 31.185000000000002,
  'tt_max_penalty': 28.957500000000003},
 2: {'canon': 264.0,
  'k': 1.4810078247291318,
  'dt_max_penalty': 36.96,
  'tt_max_penalty': 22.880000000000006},
 3: {'canon': 181.5,
  'k': 14.186717826602765,
  'dt_max_penalty': 25.41,
  'tt_max_penalty': 23.595000000000006}}

In [304]:
sm = RevenueMaximization(schedule, revenue, safe_headway=10)

In [305]:
gsa_algo = GSA(objective_function=sm.get_fitness_gsa,
               is_feasible=sm.feasible_services_times,
               r_dim=len(sm.real_boundaries),
               d_dim=0,
               boundaries=sm.boundaries)

In [306]:
gsa_algo.set_seed(seed=28)

pop_size = 20
training_history = gsa_algo.optimize(population_size=pop_size,
                                     iters=300,
                                     chaotic_constant=False,
                                     repair_solution=True,
                                     initial_population=sm.get_initial_population(pop_size))

[1, 1, 1, 1, 2, 2, 2, 2, 2, 2, 3, 3, 3, 3]
Initial population: {'real': array([[ 4.5800e+00,  1.5562e+02,  1.5992e+02,  1.8875e+02,  1.3630e+01,
         3.5860e+01,  3.8250e+01,  1.7474e+02,  1.7699e+02,  2.2000e+02,
         2.3850e+01,  1.8953e+02,  1.9164e+02,  2.3465e+02],
       [ 8.9200e+00,  1.5792e+02,  1.6194e+02,  1.8995e+02,  5.9100e+00,
         3.2080e+01,  3.5900e+01,  1.7266e+02,  1.7660e+02,  2.1982e+02,
         3.6620e+01,  1.8999e+02,  1.9199e+02,  2.3499e+02],
       [ 5.4800e+00,  1.5416e+02,  1.6095e+02,  1.8995e+02, -5.4000e-01,
         2.7750e+01,  3.8370e+01,  1.7361e+02,  1.7667e+02,  2.1993e+02,
         3.3500e+01,  1.8436e+02,  1.8658e+02,  2.3314e+02],
       [-4.9800e+00,  1.5783e+02,  1.6192e+02,  1.8992e+02,  1.1980e+01,
         3.5760e+01,  3.9770e+01,  1.7481e+02,  1.7693e+02,  2.1995e+02,
         3.5270e+01,  1.8601e+02,  1.9172e+02,  2.3486e+02],
       [ 6.6600e+00,  1.5543e+02,  1.5970e+02,  1.8925e+02,  9.5800e+00,
         3.6950e+01,  4.000

/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)


Service 1 is not feasible: 146.87101464124115 < 148
Service 1 is not feasible: 147.66526642689976 < 148
Service 1 is not feasible: 146.72817052527648 < 148
Service 1 is not feasible: 147.48710660327185 < 148
Service 3 is not feasible: 147.97459954026067 < 150
Service 1 is not feasible: 146.07328302349487 < 148
Service 1 is not feasible: 146.40142681204824 < 148
Service 3 is not feasible: 148.97334254257905 < 150
Repairing solution...
Service 3 is not feasible: 146.39535514093814 < 150
Repairing solution...
Repairing solution...
Service 3 is not feasible: 149.84326968602437 < 150
Service 1 is not feasible: 27.99283597797819 < 28
Service 3 is not feasible: 145.68668937690788 < 150
Service 2 is not feasible: 42.715120251173204 < 43
Service 3 is not feasible: 142.54201350836826 < 150
Service 3 is not feasible: 141.19517645423605 < 150
Service 3 is not feasible: 146.4242867586319 < 150
Service 1 is not feasible: 147.9335844366827 < 148
Service 2 is not feasible: 42.74423638184521 < 43
Servi

/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)


Service 1 is not feasible: 147.85503527548283 < 148
Repairing solution...
Service 1 is not feasible: 27.80361263331369 < 28
Service 1 is not feasible: 25.987996354320245 < 28
Service 1 is not feasible: 26.461251548879034 < 28
Service 1 is not feasible: 27.31274295604524 < 28
Service 1 is not feasible: 26.665566287039866 < 28
Service 1 is not feasible: 27.577948710282215 < 28
Service 1 is not feasible: 27.025071353785677 < 28
Service 1 is not feasible: 25.26913944080897 < 28
Service 1 is not feasible: 27.075658733696685 < 28
Service 1 is not feasible: 24.951882773344295 < 28
Service 1 is not feasible: 27.48954976137432 < 28
Service 1 is not feasible: 24.670968583751318 < 28
Service 1 is not feasible: 25.496034769324098 < 28
Service 1 is not feasible: 27.446852119082592 < 28
Service 1 is not feasible: 27.173295111752537 < 28
Service 2 is not feasible: 19.476351663999594 < 20
Service 1 is not feasible: 27.33189771274226 < 28
Service 3 is not feasible: 147.88176199372737 < 150
Service 1 is

...

/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site

Service 2 is not feasible: 42.99999997854101 < 43
Repairing solution...
Service 2 is not feasible: 42.99999997854101 < 43
Service 2 is not feasible: 42.99999994386397 < 43
Repairing solution...
Service 2 is not feasible: 42.99999994386397 < 43
Service 2 is not feasible: 42.99999999572174 < 43
Repairing solution...
Service 2 is not feasible: 42.99999999572174 < 43
Repairing solution...
Service 2 is not feasible: 42.9999999749985 < 43
Repairing solution...
Service 2 is not feasible: 42.9999999749985 < 43
Service 2 is not feasible: 42.999999997114145 < 43
Service 2 is not feasible: 42.999999989956194 < 43
Service 2 is not feasible: 42.999999981706054 < 43
Repairing solution...
Service 2 is not feasible: 42.999999981706054 < 43
Service 2 is not feasible: 42.99999995334957 < 43
Repairing solution...
Service 2 is not feasible: 42.99999995334957 < 43
Service 2 is not feasible: 42.99999995219562 < 43
Repairing solution...
Service 2 is not feasible: 42.99999995219562 < 43
Repairing solution...


/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site

Service 2 is not feasible: 42.99999995614513 < 43
Service 2 is not feasible: 42.9999999856947 < 43
Repairing solution...
Service 2 is not feasible: 42.9999999856947 < 43
Service 2 is not feasible: 42.99999993346884 < 43
Service 2 is not feasible: 42.99999994809107 < 43
Repairing solution...
Service 2 is not feasible: 42.999999991072144 < 43
Service 2 is not feasible: 42.99999999998579 < 43
Service 2 is not feasible: 42.9999999690684 < 43
Service 2 is not feasible: 42.99999999484476 < 43
Service 2 is not feasible: 42.99999996672082 < 43
Service 2 is not feasible: 42.9999999913029 < 43
Service 2 is not feasible: 42.99999998035048 < 43
Service 2 is not feasible: 42.99999998702563 < 43
Service 2 is not feasible: 42.999999982083494 < 43
Service 2 is not feasible: 42.999999985648 < 43
Service 2 is not feasible: 42.9999999904926 < 43
Service 2 is not feasible: 42.999999967776745 < 43
Service 2 is not feasible: 42.99999999876812 < 43
Service 2 is not feasible: 42.999999984083786 < 43
Service 2

/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/Users/uclm/PycharmProjects/GSA_M/venv/lib/python3.9/site

In [296]:
# Get last value in column 'Real' of training_history
best_solution = training_history.iloc[-1]['Real']
best_solution

array([ -9.99954243, 152.12098772, 160.63993987, 190.        ,
         7.97477125,  34.57116842,  36.9230443 , 173.54347174,
       176.95225949, 220.        ,  29.96010009, 187.79806785,
       191.9907552 , 235.        ])

In [301]:
S_i = sm.get_best_schedule({'real': best_solution, 'disrealcrete': np.array([])})

sm.get_revenue({'real': best_solution, 'discrete': S_i})

570.8469090420417

In [297]:
sm.get_best_schedule({'real': best_solution, 'discrete': np.array([])})

array([1, 1, 1])

In [298]:
sum([revenue[service]['canon'] for service in revenue])

668.25

In [299]:
training_history

Iteration     Fitness  Accuracy  ExecutionTime Discrete  \
0            0  517.014978         0       0.002577       []   
1            1  528.468346         0       0.075170       []   
2            2  548.879257         0       0.154630       []   
3            3  550.183176         0       0.233030       []   
4            4  550.183176         0       0.311096       []   
..         ...         ...       ...            ...      ...   
295        295  570.846909         0       6.411785       []   
296        296  570.846909         0       6.413651       []   
297        297  570.846909         0       6.415428       []   
298        298  570.846909         0       6.417315       []   
299        299  570.846909         0       6.419090       []   

                                                  Real  
0    [-9.999542419331794, 152.12098763169274, 160.6...  
1    [-9.999542419331794, 152.12098763169274, 160.6...  
2    [-9.999542419331794, 152.12098763169274, 160.6...  
3    [-9.999542419331794, 152.12098763169274, 160.6...  
4    [-9.999542419331794, 152.12098763169274, 160.6...  
..                                                 ...  
295  [-9.999542425505457, 152.12098771942152, 160.6...  
296  [-9.999542425505457, 152.12098771942152, 160.6...  
297  [-9.999542425505457, 152.12098771942152, 160.6...  
298  [-9.999542425505457, 152.12098771942152, 160.6...  
299  [-9.999542425505457, 152.12098771942152, 160.6...  

[300 rows x 6 columns]

In [118]:
for row in training_history.iterrows():
    sol_dis = list(row[1]['Discrete'])
    sol_real = list(row[1]['Real'])
    print(sm.get_revenue({'real': np.array(sol_real), 'discrete': np.array(sol_dis)}))
    

192.0272237680468
350.4703320438339
350.4703320438339
350.4703320438339
350.4703320438339
350.4703320438339
350.4703320438339
355.1444651642497
378.43994679619436
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.8259082813064
378.82590

In [61]:
revenue

{1: {'canon': 222.75,
  'k': 7.424686268142557,
  'dt_max_penalty': 31.185000000000002,
  'tt_max_penalty': 28.957500000000003},
 2: {'canon': 264.0,
  'k': 1.4810078247291318,
  'dt_max_penalty': 36.96,
  'tt_max_penalty': 22.880000000000006},
 3: {'canon': 181.5,
  'k': 14.186717826602765,
  'dt_max_penalty': 25.41,
  'tt_max_penalty': 23.595000000000006}}

In [ ]:
# S_i ES UNA CONSECUENCIA DE LOS TIEMPO, NO UNA VARIABLE EN SÍ MISMA.